In [1]:
import pandas as pd
import numpy as np
import nltk
import re
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import NMF
from sklearn.decomposition import LatentDirichletAllocation
from nltk.stem.lancaster import LancasterStemmer
from collections import defaultdict

In [43]:
df = pd.read_pickle("text_df_v3.pkl")
df

text  \
0       This report contains forward-looking statemen...   
1      he COVID-19 pandemic has adversely impacted, a...   
2      Our global operations expose us to risks assoc...   
3      Due to these measures we experienced significa...   
4      Accordingly, COVID-19 has negatively affected ...   
...                                                  ...   
76201  The novel coronavirus (COVID-19) was identifie...   
76202  The COVID-19 pandemic also may reduce demand f...   
76203  Moreover, measures imposed by governments and ...   
76204  The COVID-19 pandemic has also significantly i...   
76205  The ultimate magnitude of the COVID-19 pandemi...   

                                               linkToTxt      cik  \
0      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
1      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
2      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
3      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
4      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
...                                                  ...      ...   
76201  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76202  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76203  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76204  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76205  https://www.sec.gov/Archives/edgar/data/155528...  1555280   

                     company_name   filed_at form_type ticker  \
0      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
1      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
2      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
3      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
4      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
...                           ...        ...       ...    ...   
76201                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76202                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76203                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76204                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76205                 Zoetis Inc. 2020-05-06      10-Q    ZTS   

                           name       sector  
0      Agilent Technologies Inc  Health Care  
1      Agilent Technologies Inc  Health Care  
2      Agilent Technologies Inc  Health Care  
3      Agilent Technologies Inc  Health Care  
4      Agilent Technologies Inc  Health Care  
...                         ...          ...  
76201                    Zoetis  Health Care  
76202                    Zoetis  Health Care  
76203                    Zoetis  Health Care  
76204                    Zoetis  Health Care  
76205                    Zoetis  Health Care  

[76206 rows x 9 columns]

In [44]:
df.drop_duplicates(inplace=True)
df

text  \
0       This report contains forward-looking statemen...   
1      he COVID-19 pandemic has adversely impacted, a...   
2      Our global operations expose us to risks assoc...   
3      Due to these measures we experienced significa...   
4      Accordingly, COVID-19 has negatively affected ...   
...                                                  ...   
76201  The novel coronavirus (COVID-19) was identifie...   
76202  The COVID-19 pandemic also may reduce demand f...   
76203  Moreover, measures imposed by governments and ...   
76204  The COVID-19 pandemic has also significantly i...   
76205  The ultimate magnitude of the COVID-19 pandemi...   

                                               linkToTxt      cik  \
0      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
1      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
2      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
3      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
4      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
...                                                  ...      ...   
76201  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76202  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76203  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76204  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76205  https://www.sec.gov/Archives/edgar/data/155528...  1555280   

                     company_name   filed_at form_type ticker  \
0      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
1      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
2      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
3      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
4      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
...                           ...        ...       ...    ...   
76201                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76202                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76203                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76204                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76205                 Zoetis Inc. 2020-05-06      10-Q    ZTS   

                           name       sector  
0      Agilent Technologies Inc  Health Care  
1      Agilent Technologies Inc  Health Care  
2      Agilent Technologies Inc  Health Care  
3      Agilent Technologies Inc  Health Care  
4      Agilent Technologies Inc  Health Care  
...                         ...          ...  
76201                    Zoetis  Health Care  
76202                    Zoetis  Health Care  
76203                    Zoetis  Health Care  
76204                    Zoetis  Health Care  
76205                    Zoetis  Health Care  

[46848 rows x 9 columns]

In [45]:
english_stop_words = stopwords.words('english')

In [46]:
additional_stop_words = ["covid", "pandemic", "novel", "coronavirus", "global", 
                        "million", "thousand", "hundred", "billion", "quarter", "year", 
                        "january", "february", "march", "april", "may", "june", 
                        "july", "august", "september", "october", "november", "december",
                        "jan", "feb", "mar", "apr", "jun", "jul", "aug", "sep", "oct", "nov", 
                         "dec", "company", "business", "us", "also", "could"]

In [47]:
all_stop_words = english_stop_words + additional_stop_words
all_stop_words

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [48]:
def remove_numbers(text):
    return re.sub(r'\d+','', text)

In [49]:
df_clean = df.copy()
df_clean["text"] = df_clean.text.apply(remove_numbers)
df_clean

text  \
0       This report contains forward-looking statemen...   
1      he COVID- pandemic has adversely impacted, and...   
2      Our global operations expose us to risks assoc...   
3      Due to these measures we experienced significa...   
4      Accordingly, COVID- has negatively affected ou...   
...                                                  ...   
76201  The novel coronavirus (COVID-) was identified ...   
76202  The COVID- pandemic also may reduce demand for...   
76203  Moreover, measures imposed by governments and ...   
76204  The COVID- pandemic has also significantly inc...   
76205  The ultimate magnitude of the COVID- pandemic,...   

                                               linkToTxt      cik  \
0      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
1      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
2      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
3      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
4      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
...                                                  ...      ...   
76201  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76202  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76203  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76204  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76205  https://www.sec.gov/Archives/edgar/data/155528...  1555280   

                     company_name   filed_at form_type ticker  \
0      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
1      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
2      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
3      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
4      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
...                           ...        ...       ...    ...   
76201                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76202                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76203                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76204                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76205                 Zoetis Inc. 2020-05-06      10-Q    ZTS   

                           name       sector  
0      Agilent Technologies Inc  Health Care  
1      Agilent Technologies Inc  Health Care  
2      Agilent Technologies Inc  Health Care  
3      Agilent Technologies Inc  Health Care  
4      Agilent Technologies Inc  Health Care  
...                         ...          ...  
76201                    Zoetis  Health Care  
76202                    Zoetis  Health Care  
76203                    Zoetis  Health Care  
76204                    Zoetis  Health Care  
76205                    Zoetis  Health Care  

[46848 rows x 9 columns]

In [50]:
vectorizer = TfidfVectorizer(stop_words=all_stop_words, min_df=10, ngram_range=(1,2))
doc_word = vectorizer.fit_transform(df_clean.text)
doc_word.shape

(46848, 46739)

In [51]:
nmf_model = NMF(7)
doc_topic = nmf_model.fit_transform(doc_word)
doc_topic.shape

(46848, 7)

In [52]:
topic_word = nmf_model.components_
topic_word.shape

(7, 46739)

In [53]:
words = vectorizer.get_feature_names()
t = nmf_model.components_.argsort(axis=1)[:,-1:-20:-1]
topic_words = [[words[e] for e in l] for l in t]
topic_words

[['customers',
  'including',
  'health',
  'employees',
  'products',
  'restrictions',
  'demand',
  'continue',
  'measures',
  'travel',
  'impact',
  'spread',
  'supply',
  'world',
  'economic',
  'significant',
  'work',
  'actions',
  'services'],
 ['months',
  'primarily',
  'sales',
  'ended',
  'months ended',
  'due',
  'lower',
  'compared',
  'net',
  'offset',
  'decreased',
  'decrease',
  'three',
  'partially',
  'partially offset',
  'primarily due',
  'costs',
  'nine',
  'nine months'],
 ['statements',
  'forward looking',
  'looking',
  'forward',
  'looking statements',
  'risks',
  'factors',
  'report',
  'form',
  'risk',
  'risk factors',
  'uncertainties',
  'report form',
  'risks uncertainties',
  'future',
  'item',
  'estimates',
  'actual',
  'results'],
 ['results',
  'results operations',
  'operations',
  'financial',
  'condition',
  'financial condition',
  'adversely',
  'operations financial',
  'impact',
  'condition results',
  'adverse',
  'a

In [54]:
df['topic'] = doc_topic.argmax(axis=1)
df

text  \
0       This report contains forward-looking statemen...   
1      he COVID-19 pandemic has adversely impacted, a...   
2      Our global operations expose us to risks assoc...   
3      Due to these measures we experienced significa...   
4      Accordingly, COVID-19 has negatively affected ...   
...                                                  ...   
76201  The novel coronavirus (COVID-19) was identifie...   
76202  The COVID-19 pandemic also may reduce demand f...   
76203  Moreover, measures imposed by governments and ...   
76204  The COVID-19 pandemic has also significantly i...   
76205  The ultimate magnitude of the COVID-19 pandemi...   

                                               linkToTxt      cik  \
0      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
1      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
2      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
3      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
4      https://www.sec.gov/Archives/edgar/data/109087...  1090872   
...                                                  ...      ...   
76201  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76202  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76203  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76204  https://www.sec.gov/Archives/edgar/data/155528...  1555280   
76205  https://www.sec.gov/Archives/edgar/data/155528...  1555280   

                     company_name   filed_at form_type ticker  \
0      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
1      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
2      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
3      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
4      AGILENT TECHNOLOGIES, INC. 2020-12-17      10-K      A   
...                           ...        ...       ...    ...   
76201                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76202                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76203                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76204                 Zoetis Inc. 2020-05-06      10-Q    ZTS   
76205                 Zoetis Inc. 2020-05-06      10-Q    ZTS   

                           name       sector  topic  
0      Agilent Technologies Inc  Health Care      2  
1      Agilent Technologies Inc  Health Care      3  
2      Agilent Technologies Inc  Health Care      0  
3      Agilent Technologies Inc  Health Care      0  
4      Agilent Technologies Inc  Health Care      0  
...                         ...          ...    ...  
76201                    Zoetis  Health Care      0  
76202                    Zoetis  Health Care      3  
76203                    Zoetis  Health Care      3  
76204                    Zoetis  Health Care      5  
76205                    Zoetis  Health Care      3  

[46848 rows x 10 columns]

In [55]:
multivalue_dict = defaultdict(list)
for inx, row in df.iterrows():
    multivalue_dict[row['topic']].append(row['text'])

In [42]:
multivalue_dict

defaultdict(list,
            {0: [" Both our domestic and international operations have been and continue to be affected by the ongoing global pandemic of a novel strain of coronavirus (“COVID-19”) and the resulting volatility and uncertainty it has caused in the U.S. and international markets. In March 2020, the World Health Organization declared COVID-19 a pandemic and recommended containment and mitigation measures worldwide.  As a result, hospitals and testing laboratories have halted certain elective medical procedures, which had an adverse effect on our customers' business. In the latter part of our second quarter, the academia and government markets revenue was negatively affected by delays in installations due to laboratory closures in Europe and the Americas. The chemical and energy market has also been negatively impacted by the global slowdown in economic activity associated with measures put in place to slow the pandemic. The COVID-19 pandemic has caused significant volati